In [1]:
import pandas as pd
import EDA

In [2]:
import re
import numpy as np
import matplotlib.pyplot as plt
import urllib.request
from collections import Counter
from konlpy.tag import Okt
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

# 학습용 데이터 전처리

In [3]:
nsmc_train_df = pd.read_excel('train.xlsx')

In [4]:
X = nsmc_train_df.dropna()

In [5]:
X['clean'] = X['reviews'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")
X['clean'].replace('', np.nan, inplace=True)
print(X.isnull().sum())

id         0
reviews    0
target     0
clean      0
dtype: int64


C:\Users\ParkJeongSu\AppData\Local\Temp\ipykernel_11256\323574154.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  X['clean'] = X['reviews'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")
C:\Users\ParkJeongSu\AppData\Local\Temp\ipykernel_11256\323574154.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X['clean'] = X['reviews'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")
C:\Users\ParkJeongSu\AppData\Local\Temp\ipykernel_11256\323574154.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X['clean'].replace('', np.nan, inplace=True)


In [6]:
X['clean']

0                                           조아요 처음구입 싸게햇어요
1         생각보다 잘 안돼요 매지 바른지 하루밖에 안됐는데ㅠㅠ 천원가량 주고 사기 너무 아깝네요
2        디자인은괜찮은데 상품이 금이가서 교환했는데 두번째받은상품도 까져있고 안쪽에 금이가져...
3        기전에 이 제품말고 이마트 트레이더스에서만 팔던 프리미엄 제품을 사용했었습니다 샘플...
4                                         튼튼하고 손목을 잘 받쳐주네요
                               ...                        
24995                    일단향이너무너무좋은데지속력만좋다면좋겠지만워낙저렴해그래도좋아여
24996           동일한 업체에서 발송하고 한 상자로 배송되었는데 택배비는 이중 처리되었습니다
24997                                향이 좋아요 다른 향도 시켜보고 싶어요
24998                펼쳐보니 끝부분쯤에 정도 찟어져 있습니다 날짜관계로 구냥 사용합니다
24999                                     호호애미 제품은 늘 믿고 써요
Name: clean, Length: 24999, dtype: object

In [7]:
X

id                                            reviews  target  \
0          0                                     조아요 처음구입 싸게햇어요       2   
1          1  생각보다 잘 안돼요 매지 바른지 하루밖에 안됐는데ㅠㅠ 25천원가량 주고 사기 너무 ...       1   
2          2  디자인은괜찮은데 상품이 금이가서 교환했는데 두번째받은상품도 까져있고 안쪽에 금이가져...       2   
3          3  기전에 이 제품말고 이마트 트레이더스에서만 팔던 프리미엄 제품을 사용했었습니다. 샘...       2   
4          4                                  튼튼하고 손목을 잘 받쳐주네요~       5   
...      ...                                                ...     ...   
24995  24995                일단향이너무너무좋은데지속력만좋다면좋겠지만..워낙저렴해그래도좋아여       5   
24996  24996        동일한 업체에서 발송하고 한 상자로 배송되었는데 택배비는 이중 처리되었습니다.       2   
24997  24997                            향이 좋아요!! 다른 향도 시켜보고 싶어요       4   
24998  24998          펼쳐보니 끝부분쯤에 50cm정도 찟어져 있습니다 날짜관계로 구냥 사용합니다       2   
24999  24999                                   호호애미 제품은 늘 믿고 써요       5   

                                                   clean  
0                                         조아요 처음구입 싸게햇어요  
1       생각보다 잘 안돼요 매지 바른지 하루밖에 안됐는데ㅠㅠ 천원가량 주고 사기 너무 아깝네요  
2      디자인은괜찮은데 상품이 금이가서 교환했는데 두번째받은상품도 까져있고 안쪽에 금이가져...  
3      기전에 이 제품말고 이마트 트레이더스에서만 팔던 프리미엄 제품을 사용했었습니다 샘플...  
4                                       튼튼하고 손목을 잘 받쳐주네요  
...                                                  ...  
24995                  일단향이너무너무좋은데지속력만좋다면좋겠지만워낙저렴해그래도좋아여  
24996         동일한 업체에서 발송하고 한 상자로 배송되었는데 택배비는 이중 처리되었습니다  
24997                              향이 좋아요 다른 향도 시켜보고 싶어요  
24998              펼쳐보니 끝부분쯤에 정도 찟어져 있습니다 날짜관계로 구냥 사용합니다  
24999                                   호호애미 제품은 늘 믿고 써요  

[24999 rows x 4 columns]

In [9]:
rating4Data = X[X['target'] == 4]['clean']

In [11]:
rating4Data

13                                         너무 잘사용했어요 감사합니다
15                                다른거는 다만족하는데 나사부분이ㅈ맘엥ㄴ들어서
24                                          깨끗하게 정리되었어요 굿굿
32                         색깔이랑 넘 이쁘고 팔걸이가 넓어 편하고 쿠션감도 좋아요
59       좋아요 여름에는 속옷입고 나시입고 하면 너무 더운데이 나시는 안에 캡이 있어서 따로...
                               ...                        
24937                                  자전거 라이딩 할때 쓸건데 ㅈㅎ아요
24942                            재구매 구입하고 넘 편해서 지인한테 선물했어요
24967                              기저귀랑 손수건 등등 정리하려고 구입했어용
24968    유튜버님 추천 보고 바로 산건데 주변 사람들 한테 이거 좋다고 백번씩 설명하고 다녔...
24997                                향이 좋아요 다른 향도 시켜보고 싶어요
Name: clean, Length: 2500, dtype: object

In [13]:
result = []

for i in rating4Data.to_list():
    result.append(EDA.EDA(i,alpha_sr=0.1, alpha_ri=0.1, alpha_rs=0.4, p_rd=0.4,num_aug = 4))

['감사합니다 잘사용했어요 너무', '너무 잘사용했어요 감사합니다', '너무 잘사용했어요 감사합니다', '너무 잘사용했어요 감사합니다', '너무 잘사용했어요 감사합니다']
['나사부분이ㅈ맘엥ㄴ들어서', '다른거는 다만족하는데 나사부분이ㅈ맘엥ㄴ들어서', '다만족하는데 다른거는 나사부분이ㅈ맘엥ㄴ들어서', '다른거는 다만족하는데 나사부분이ㅈ맘엥ㄴ들어서', '다른거는 다만족하는데 나사부분이ㅈ맘엥ㄴ들어서']
['정리되었어요 깨끗하게 굿굿', '깨끗하게 정리되었어요 굿굿', '깨끗하게 정리되었어요 굿굿', '정리되었어요 깨끗하게 굿굿', '깨끗하게 정리되었어요 굿굿']
['색깔이랑 넘 이쁘고 팔걸이가 넓어 편하고 쿠션감도 좋아요', '색깔이랑 넘 이쁘고 쿠션감도 넓어 좋아요 편하고 팔걸이가', '색깔이랑 넘 팔걸이가 넓어 편하고 좋아요', '색깔이랑 넘 이쁘고 팔걸이가 넓어 편하고 쿠션감도 좋아요', '색깔이랑 넘 이쁘고 팔걸이가 넓어 편하고 쿠션감도 좋아요']
['좋아요 되고 속옷입고 나시입고 캡이 좋네요 더운데이 나시는 안에 너무 있어서 속옷 따로 안입어도 편하고 여름에는 하면', '좋아요 여름에는 좋네요 나시입고 하면 캡이 안입어도 나시는 안에 너무 편하고 되고 속옷 더운데이 있어서 따로 속옷입고', '좋아요 여름에는 속 속옷입고 나시입고 하면 너무 더운데이 나시는 안에 캡이 있어서 따로 속옷 안입어도 되고 편하고 좋네요', '좋아요 속옷입고 하면 캡이 있어서 따로 속옷 안입어도 되고 편하고 좋네요', '좋아요 여름에는 속옷입고 나시입고 하면 너무 더운데이 나시는 안에 캡이 있어서 따로 속옷 안입어도 되고 편하고 좋네요']
['배송도 빠르고 아이가 색깔이랑 쓰기에도 편하다고 하네요', '배송도 빠르고 아이가 색깔이랑 쓰기에도 편하다고 하네요', '배송도 아이가 색깔이랑 쓰기에도', '아이가 편하다고 배송도 색깔이랑 쓰기에도 빠르고 하네요', '배송도 빠르고 아이가 색깔이랑 쓰기에도 편하다고 하네요']
['좋아요ㅠ잘쓰고닛어요', '좋아요ㅠ잘쓰고닛어요', '좋아요ㅠ잘쓰

# 테스트 데이터 전처리

In [10]:
X_test = pd.read_excel('test.xlsx')

In [7]:
X_test['clean'] = X_test['reviews'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")
X_test['clean'].replace('', np.nan, inplace=True)

C:\Users\ParkJeongSu\AppData\Local\Temp\ipykernel_14332\630216630.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  X_test['clean'] = X_test['reviews'].str.replace("[^ㄱ-ㅎㅏ-ㅣ가-힣 ]","")


0                                           조아요 처음구입 싸게햇어요
1         생각보다 잘 안돼요 매지 바른지 하루밖에 안됐는데ㅠㅠ 천원가량 주고 사기 너무 아깝네요
2        디자인은괜찮은데 상품이 금이가서 교환했는데 두번째받은상품도 까져있고 안쪽에 금이가져...
3        기전에 이 제품말고 이마트 트레이더스에서만 팔던 프리미엄 제품을 사용했었습니다 샘플...
4                                         튼튼하고 손목을 잘 받쳐주네요
                               ...                        
24995                    일단향이너무너무좋은데지속력만좋다면좋겠지만워낙저렴해그래도좋아여
24996           동일한 업체에서 발송하고 한 상자로 배송되었는데 택배비는 이중 처리되었습니다
24997                                향이 좋아요 다른 향도 시켜보고 싶어요
24998                펼쳐보니 끝부분쯤에 정도 찟어져 있습니다 날짜관계로 구냥 사용합니다
24999                                     호호애미 제품은 늘 믿고 써요
Name: clean, Length: 24999, dtype: object

In [23]:
Xdata = X['clean'].to_list()

In [24]:
result = []

In [28]:
for i in Xdata:
    print(EDA.EDA(i,alpha_sr=0.1, alpha_ri=0.1, alpha_rs=0.4, p_rd=0.4,num_aug = 4))

['조아요', '조아요 처음구입 싸게햇어요', '조아요 처음구입 싸게햇어요', '조아요 처음구입', '조아요 처음구입 싸게햇어요']
['사기 잘 아깝네요 매지 바른지 하루밖에 생각보다 천원가량 안돼요 안됐는데ㅠㅠ 너무 주고', '생각보다 주고 천원가량 바른지 잘 하루밖에 안됐는데ㅠㅠ 안돼요 매지 사기 너무 아깝네요', '생각보다 잘 안돼요 바른지 하루밖에 안됐는데ㅠㅠ 주고 너무 아깝네요', '생각보다 잘 안돼요 매지 바른지 사 하루밖에 안됐는데ㅠㅠ 천원가량 주고 사기 너무 아깝네요', '생각보다 잘 안돼요 매지 바른지 하루밖에 안됐는데ㅠㅠ 천원가량 주고 사기 너무 아깝네요']
['디자인은괜찮은데 상품이 금이가서 교환했는데 두번째받은상품도 까져있고 안쪽에 금이가져있네요 ㅠ 귀찮아서 그냥쓰려구요 배송기사님은 친절하셨어요', '디자인은괜찮은데 상품이 금이가서 교환했는데 두번째받은상품도 까져있고 안쪽에 금이가져있네요 ㅠ 귀찮아서 그냥쓰려구요 배송기사님은 친절하셨어요', '디자인은괜찮은데 교환했는데 두번째받은상품도 금이가져있네요 ㅠ', '디자인은괜찮은데 상품이 금이가서 안쪽에 두번째받은상품도 까져있고 그냥쓰려구요 금이가져있네요 교환했는데 귀찮아서 ㅠ 배송기사님은 친절하셨어요', '디자인은괜찮은데 상품이 금이가서 교환했는데 두번째받은상품도 까져있고 안쪽에 금이가져있네요 ㅠ 귀찮아서 그냥쓰려구요 배송기사님은 친절하셨어요']
['기전에 이마트 트레이더스에서만 팔던 프리미엄 제품을 써보고 마음에 구매해 같은 할수 없이 구매했는데요 감고나도 머리가 개운하지 않고', '기전에 이 제품을 저랑은 트레이더스에서만 플러스를 프리미엄 써보고 사용했었습니다 같은 감고나도 마음에 들어 이마트 사용중 구매했는데요 구매해 않고 않아 샘플 팔지 팔던 할수 제품말고 머리가 개운하지 없이 간지럽네요 제품을 잘 안맞는듯해요', '기전에 이 제품말고 이마트 트레이더스에서만 팔던 프리미엄 제품을 사용했었습니다 샘플 써보고 마음에 들어 구매해 사용중 같은 제품을 팔지 않아 할수 없이 플러스를 구매했는데요 

In [26]:
result

array([], dtype=float64)